# Задача
Общая задача проекта:

Разработать модель, которая будет классифицировать трафик на нормальный и злонамеренный. При этом модель должна работать максимально качественно, так как цена ошибки может быть очень высока. Оценить качество модели по различным метрикам классификации: precision, recall, f1_score, accuracy. Разработать REST API сервис, который будет принимать на вход данные трафика и возвращать класс этого трафика.

В рамках ноутбука проведем минимальный анализ данных и попробуем обучить модель. Если метрики окажутся высокими, перейдем к реализации модульного проекта.

In [23]:
import pandas as pd
import numpy as np

from catboost import CatBoostClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import recall_score, f1_score, accuracy_score, precision_score, roc_auc_score
from ydata_profiling import ProfileReport

In [2]:
try:
    initial_data = pd.read_csv('network_traffic_data.csv')
except:
    raise Exception('Check the file')

## Знакомство с данными

In [3]:
initial_data.head()

Destination Port   Flow Duration   Total Fwd Packets  \
0                 80         5480074                   3   
1                443          711977                   9   
2                 53          153398                   2   
3                 53           57660                   1   
4               8446             767                   3   

    Total Backward Packets  Total Length of Fwd Packets  \
0                        1                           12   
1                       10                          703   
2                        2                           80   
3                        1                           46   
4                        1                           43   

    Total Length of Bwd Packets   Fwd Packet Length Max  \
0                             0                       6   
1                          3950                     267   
2                           224                      40   
3                           128                      46   
4                             6                      31   

    Fwd Packet Length Min   Fwd Packet Length Mean   Fwd Packet Length Std  \
0                       0                    4.000                   3.465   
1                       0                   78.100                 103.300   
2                      40                   40.000                   0.000   
3                      46                   46.000                   0.000   
4                       6                   14.336                  14.440   

   ...   min_seg_size_forward  Active Mean   Active Std   Active Max  \
0  ...                     20          0.0          0.0            0   
1  ...                     32          0.0          0.0            0   
2  ...                     20          0.0          0.0            0   
3  ...                     20          0.0          0.0            0   
4  ...                     20          0.0          0.0            0   

    Active Min  Idle Mean   Idle Std   Idle Max   Idle Min   Label  
0            0        0.0        0.0          0          0  BENIGN  
1            0        0.0        0.0          0          0  BENIGN  
2            0        0.0        0.0          0          0  BENIGN  
3            0        0.0        0.0          0          0  BENIGN  
4            0        0.0        0.0          0          0  BENIGN  

[5 rows x 79 columns]

In [4]:
initial_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 539616 entries, 0 to 539615
Data columns (total 79 columns):
 #   Column                        Non-Null Count   Dtype  
---  ------                        --------------   -----  
 0    Destination Port             539616 non-null  int64  
 1    Flow Duration                539616 non-null  int64  
 2    Total Fwd Packets            539616 non-null  int64  
 3    Total Backward Packets       539616 non-null  int64  
 4   Total Length of Fwd Packets   539616 non-null  int64  
 5    Total Length of Bwd Packets  539616 non-null  int64  
 6    Fwd Packet Length Max        539616 non-null  int64  
 7    Fwd Packet Length Min        539616 non-null  int64  
 8    Fwd Packet Length Mean       539616 non-null  float64
 9    Fwd Packet Length Std        539616 non-null  float64
 10  Bwd Packet Length Max         539616 non-null  int64  
 11   Bwd Packet Length Min        539616 non-null  int64  
 12   Bwd Packet Length Mean       539616 non-nul

In [5]:
initial_data.describe()

Destination Port   Flow Duration   Total Fwd Packets  \
count      539616.000000    5.396160e+05       539616.000000   
mean         5563.061394    2.106693e+07            6.119972   
std         14921.262751    3.812172e+07          345.109317   
min             0.000000   -1.200000e+01            1.000000   
25%            80.000000    7.300000e+01            1.000000   
50%            80.000000    4.973900e+04            2.000000   
75%           443.000000    1.064030e+07            6.000000   
max         65533.000000    1.200000e+08       200755.000000   

        Total Backward Packets  Total Length of Fwd Packets  \
count            539616.000000                 5.396160e+05   
mean                  5.985495                 4.082371e+02   
std                 463.490949                 7.478351e+03   
min                   0.000000                 0.000000e+00   
25%                   1.000000                 2.000000e+00   
50%                   2.000000                 4.400000e+01   
75%                   5.000000                 3.200000e+02   
max              270686.000000                 2.866110e+06   

        Total Length of Bwd Packets   Fwd Packet Length Max  \
count                  5.396160e+05           539616.000000   
mean                   7.999779e+03              169.449966   
std                    1.014442e+06              560.533869   
min                    0.000000e+00                0.000000   
25%                    0.000000e+00                2.000000   
50%                    1.050000e+02               23.000000   
75%                    8.216250e+03              272.000000   
max                    5.910000e+08            24820.000000   

        Fwd Packet Length Min   Fwd Packet Length Mean  \
count           539616.000000            539616.000000   
mean                11.855382                44.681011   
std                 60.961661               150.873880   
min                  0.000000                 0.000000   
25%                  0.000000                 2.000000   
50%                  0.000000                11.220000   
75%                  6.000000                48.560000   
max               2065.000000              5940.000000   

        Fwd Packet Length Std  ...   act_data_pkt_fwd   min_seg_size_forward  \
count           539616.000000  ...      539616.000000           5.396160e+05   
mean                59.525095  ...           2.946516          -2.429314e+03   
std                217.729412  ...         267.510434           1.052329e+06   
min                  0.000000  ...           0.000000          -5.368707e+08   
25%                  0.000000  ...           0.000000           2.000000e+01   
50%                  0.000000  ...           1.000000           2.400000e+01   
75%                 91.700000  ...           2.000000           3.200000e+01   
max               7050.000000  ...      192491.000000           1.380000e+02   

        Active Mean    Active Std    Active Max    Active Min     Idle Mean  \
count  5.396160e+05  5.396160e+05  5.396160e+05  5.396160e+05  5.396160e+05   
mean   1.154984e+05  4.037570e+04  1.672882e+05  8.983017e+04  1.610155e+07   
std    7.787530e+05  4.347032e+05  1.059626e+06  7.099710e+05  3.315463e+07   
min    0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
25%    0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
50%    0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
75%    6.000000e+00  0.000000e+00  6.000000e+00  5.000000e+00  7.125041e+06   
max    1.020000e+08  6.350000e+07  1.020000e+08  1.020000e+08  1.200000e+08   

           Idle Std      Idle Max      Idle Min  
count  5.396160e+05  5.396160e+05  5.396160e+05  
mean   9.585649e+05  1.687227e+07  1.539150e+07  
std    6.461275e+06  3.403851e+07  3.295695e+07  
min    0.000000e+00  0.000000e+00  0.000000e+00  
25%    0.000000e+00  0.000000e+00  0.000000e+00  
50%    0.000000e+00  0.000000e+00  0.00

Видим, что есть пропуски в столбце Flow Bytes/s, что вероятно означает скорость потока данных. Этот показатель можно будет безболезненно заполнить медианой. Также в заголовках датасета есть лишние пробелы.

In [6]:
# посмотрим, как распределяются классы целевого признака
initial_data['Label'].value_counts()

BENIGN                        240000
DoS Hulk                      115974
PortScan                       79660
DDoS                           64366
DoS GoldenEye                  10293
FTP-Patator                     7938
SSH-Patator                     5897
DoS slowloris                   5796
DoS Slowhttptest                5499
Bot                             1966
Web Attack � Brute Force        1507
Web Attack � XSS                 652
Infiltration                      36
Web Attack � Sql Injection        21
Heartbleed                        11
Name: Label, dtype: int64

Классы не очень-то равны, поэтому при оценивании больше внимания будем обращать на взвешенные оценки.

In [7]:
# посмотрим порты
initial_data[' Destination Port'].value_counts()

80       229165
53       101315
443       53430
21         8638
22         7245
          ...  
62846         1
61995         1
64275         1
41909         1
3051          1
Name:  Destination Port, Length: 24926, dtype: int64

Порты кажутся категориальным признаком, так как их не имеет смысла оценивать в среднем или проводить арифметические операции. Так как будем использовать Catboost, то при обучении выделим, что этот признак категориальный.

In [8]:
# построим минимальный профайлер для всего остального, так как датасет большой
profile = ProfileReport(initial_data, title='Pandas Profiling Report', minimal=True)
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Есть скошенные, константные и нулевые значения, но пока что ничего однозначно ломающего.

## Предобработка данных

In [9]:
# удалим лишние пробелы из названий признаков
def strip_spaces(df):
    new_columns = {}
    for col in df.columns:
        new_columns[col] = col.strip()
    df = df.rename(columns=new_columns)
    return df

In [10]:
# сделаем копию датасета
data = initial_data.copy()

In [11]:
data = strip_spaces(data)

In [12]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 539616 entries, 0 to 539615
Data columns (total 79 columns):
 #   Column                       Non-Null Count   Dtype  
---  ------                       --------------   -----  
 0   Destination Port             539616 non-null  int64  
 1   Flow Duration                539616 non-null  int64  
 2   Total Fwd Packets            539616 non-null  int64  
 3   Total Backward Packets       539616 non-null  int64  
 4   Total Length of Fwd Packets  539616 non-null  int64  
 5   Total Length of Bwd Packets  539616 non-null  int64  
 6   Fwd Packet Length Max        539616 non-null  int64  
 7   Fwd Packet Length Min        539616 non-null  int64  
 8   Fwd Packet Length Mean       539616 non-null  float64
 9   Fwd Packet Length Std        539616 non-null  float64
 10  Bwd Packet Length Max        539616 non-null  int64  
 11  Bwd Packet Length Min        539616 non-null  int64  
 12  Bwd Packet Length Mean       539616 non-null  float64
 13 

In [13]:
# обозначим категориальные и численные значения, а также признаки и таргет
cat_features = ['Destination Port']
num_features = data.drop(['Destination Port', 'Label'], axis=1).columns
features = data.drop('Label', axis=1)
target = data['Label']

In [14]:
# проверим пропуски
data['Flow Bytes/s'].isna().sum()

488

In [15]:
data['Flow Bytes/s'] = data['Flow Bytes/s'].fillna(data['Flow Bytes/s'].median())

In [16]:
data['Flow Bytes/s'].isna().sum()

0

In [17]:
data.isna().sum().sum()

0

In [18]:
# разбиваем на две выборки
features_train, features_valid, target_train, target_valid = train_test_split(
    features, target, test_size=0.25, random_state=12345, shuffle=True)

In [19]:
(features_train.shape, features_valid.shape, target_train.shape, target_valid.shape)

((404712, 78), (134904, 78), (404712,), (134904,))

In [20]:
# обучим модель
model = CatBoostClassifier(loss_function='MultiClass', iterations=100, depth=5, learning_rate=0.5, thread_count=-1)
model.fit(features_train, target_train, cat_features=cat_features, verbose=10)

0:	learn: 0.4753461	total: 877ms	remaining: 1m 26s
10:	learn: 0.1381596	total: 7.22s	remaining: 58.4s
20:	learn: 0.0587434	total: 13.7s	remaining: 51.7s
30:	learn: 0.0284496	total: 19.9s	remaining: 44.3s
40:	learn: 0.0255453	total: 25.9s	remaining: 37.3s
50:	learn: 0.0232466	total: 31.9s	remaining: 30.7s
60:	learn: 0.0214477	total: 38s	remaining: 24.3s
70:	learn: 0.0196806	total: 43.9s	remaining: 17.9s
80:	learn: 0.0178024	total: 50.4s	remaining: 11.8s
90:	learn: 0.0164461	total: 56.7s	remaining: 5.61s
99:	learn: 0.0150811	total: 1m 2s	remaining: 0us


In [21]:
# посчитаем предсказания
preds = model.predict(features_valid, thread_count=-1)
predictions = model.predict_proba(features_valid)

In [22]:
# оценим метрики
print('Micro Precision: {:.2f}'.format(precision_score(target_valid, preds, average='micro')))
print('Micro Recall: {:.2f}'.format(recall_score(target_valid, preds, average='micro')))
print('Micro F1-score: {:.2f}\n'.format(f1_score(target_valid, preds, average='micro')))

print('Macro Precision: {:.2f}'.format(precision_score(target_valid, preds, average='macro')))
print('Macro Recall: {:.2f}'.format(recall_score(target_valid, preds, average='macro')))
print('Macro F1-score: {:.2f}'.format(f1_score(target_valid, preds, average='macro')))
print('Macro ROC AUC: {:.2f}\n'.format(roc_auc_score(target_valid, predictions, average='macro', multi_class='ovo')))

print('Weighted Precision: {:.2f}'.format(precision_score(target_valid, preds, average='weighted')))
print('Weighted Recall: {:.2f}'.format(recall_score(target_valid, preds, average='weighted')))
print('Weighted F1-score: {:.2f}'.format(f1_score(target_valid, preds, average='weighted')))
print('Weighted ROC AUC: {:.2f}\n'.format(roc_auc_score(target_valid, predictions, average='weighted', multi_class='ovo')))

Micro Precision: 1.00
Micro Recall: 1.00
Micro F1-score: 1.00

Macro Precision: 0.90
Macro Recall: 0.83
Macro F1-score: 0.83
Macro ROC AUC: 0.99

Weighted Precision: 1.00
Weighted Recall: 1.00
Weighted F1-score: 1.00
Weighted ROC AUC: 1.00



Как видим, метрики сразу получились отличные, только макро отстает, что скорее всего связанно с дисбалансом классов, но нам будет более интересно взвешенное значение. Учитывая текущие показатели, можно перейти к созданию модульного REST-сервиса.